In [1]:
# import libraries
import pandas as pd
import io

# mount google drive to access files
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
df = pd.read_csv('/content/drive/MyDrive/Sounding_Spirit/location_processed.csv')
df['location'] = df['location'].astype(str)
df

PID ssdl:notation                        location  Date  \
0     1850-Missou-EMU    Four-shape                  Cincinnati, OH  1850   
1     1850-Missou-EMU    Four-shape                  Cincinnati, OH  1850   
2     1852-Collec-EMU           Nil                    Richmond, VA  1852   
3     1852-Peters-EMU         Round  Saint Louis, MO;Cincinnati, OH  1851   
4     1852-Reviva-EMU           Nil                   Baltimore, MD  1852   
...               ...           ...                             ...   ...   
1294  1859-Narrat-UMI           NaN                             nan   NaN   
1295  1891-Otterb-UMI           NaN                             nan   NaN   
1296  1882-Songsf-UMI           NaN                             nan   NaN   
1297  1879-Gospel-UMI           NaN                             nan   NaN   
1298  1877-Grandc-UMI           NaN                             nan   NaN   

                 Long           Lati  
0              -84.45          39.15  
1              -84.45          39.15  
2              -77.45          37.55  
3     -90.1833;-84.45  38.6167;39.15  
4               -76.6        39.2833  
...               ...            ...  
1294                0              0  
1295                0              0  
1296                0              0  
1297                0              0  
1298                0              0  

[1299 rows x 6 columns]

Solutions to solve geopandas being very slow (https://caellwyn.medium.com/folium-can-be-very-slow-with-a-lot-of-data-368aee3655e2)<br/>
random sampling<br/>
filter specific data<br/>
geopandas (https://geopandas.org/en/stable/docs/user_guide/mapping.html)<br/>

Notes: the newest version is a html generated using python script

In [3]:
import geopy
import folium

object=geopy.Nominatim(user_agent="Nikki")
center=object.geocode("Atlanta, GA")
map = folium.Map(location=[center.latitude,center.longitude], zoom_start=4)

dict = {}

for x in df.index:
  location = df.loc[x, "location"].split(";")
  lo = df.loc[x, "Long"].split(";")
  la = df.loc[x, "Lati"].split(";")
  # print(df.loc[x, "PID"])
  # print(location)
  # print(lo)
  # print(la)
  for i in range (0,len(location)):
    if i>=len(lo) and i>=len(la):
      lo.append(0)
      la.append(0)
    # check edge cases
    if lo[i] == 0 and la[i] == 0:
      if location[i] == "Dale City, PA":
        lo[i] = -77.342350
        la[i] = 38.648284
        continue
      if location[i] == '':
        continue
      # print("location:",location[i])
      loc = object.geocode(location[i])
      lo[i] = loc.longitude
      la[i] = loc.latitude
    coor = str(lo[i])+";"+str(la[i])
    if coor not in dict:
      dict[coor]=location[i]
    dict[coor]='<a href="google.com">link text</a>'+dict[coor]+"<br/>"+df.loc[x, "PID"]

df2=pd.DataFrame(dict.items())
for x in df2.index:
  coor = df2.loc[x,0]
  lo=coor.split(";")[0]
  la=coor.split(";")[1]
  # print(len(df2.loc[x,1].split("<br/>"))-1)
  folium.Marker([la,lo], popup=folium.map.Popup(html=df2.loc[x,1],max_width=100)).add_to(map)
map

In [4]:
# generate the time periods and corresponding color
start = 1850
end = 1937

colors = [
    # "white",
          "lightred", # 1850 - 1893
          "red",      # 1893 - 1937
          "darkred",  # 1937 - 1980
          "black"]    # 1980 - 2024

seg = []
for x in range (0,len(colors)):
  seg.append(int(start+(x+1)*(end-start)/len(colors)))
print(seg)

[1871, 1893, 1915, 1937]


In [6]:
# plot all dots and color them based on year published
map_colored = folium.Map(location=[center.latitude,center.longitude], zoom_start=4)

for x in df.index:
  location = df.loc[x, "location"].split(";")
  lo = df.loc[x, "Long"].split(";")
  la = df.loc[x, "Lati"].split(";")

  # print(df.loc[x, "PID"])
  # print(location)
  # print(lo)
  # print(la)

  color = ""

  if str(df.loc[x,"Date"]) == 'nan':
    color = "red"
  else:
    for i in range (0,len(colors)):
      if df.loc[x,"Date"]<str(seg[i]):
        color = colors[i]
        break
  if color == "":
    color = "red"
  # print("color:",color)

  for i in range (0,len(location)):
    if i>=len(lo) and i>=len(la):
      lo.append(0)
      la.append(0)
    if lo[i] == 0 and la[i] == 0:
      if location[i] == "Dale City, PA":
        lo[i] = -77.342350
        la[i] = 38.648284
        continue
      if location[i] == '':
        continue
      # print("location:",location[i])
      loc = object.geocode(location[i])
      lo[i] = loc.longitude
      la[i] = loc.latitude
    folium.Marker([la[i],lo[i]],
                  icon = folium.map.Icon(color=color),
                  popup=folium.map.Popup(html=df.loc[x, "PID"]+"<br/>"+location[i],max_width=100)
                  ).add_to(map)
map

In [5]:
# plot dots in a period
map_colored = folium.Map(location=[center.latitude,center.longitude], zoom_start=4)

for x in df.index:
  location = df.loc[x, "location"].split(";")
  lo = df.loc[x, "Long"].split(";")
  la = df.loc[x, "Lati"].split(";")

  # print(df.loc[x, "PID"])
  # print(location)
  # print(lo)
  # print(la)

  color = ""

  if str(df.loc[x,"Date"]) == 'nan':
    color = "red"
  else:
    for i in range (0,len(colors)):
      if df.loc[x,"Date"]<str(seg[i]):
        color = colors[i]
        break
  if color == "":
    color = "red"
  # print("color:",color)

  if color != colors[3]: # decides which time period will be plotted
    continue

  for i in range (0,len(location)):
    if i>=len(lo) and i>=len(la):
      lo.append(0)
      la.append(0)
    if lo[i] == 0 and la[i] == 0:
      if location[i] == "Dale City, PA":
        lo[i] = -77.342350
        la[i] = 38.648284
        continue
      if location[i] == '':
        continue
      # print("location:",location[i])
      loc = object.geocode(location[i])
      lo[i] = loc.longitude
      la[i] = loc.latitude
    folium.Marker([la[i],lo[i]],
                  icon = folium.map.Icon(color=color),
                  popup=folium.map.Popup(html=df.loc[x, "PID"]+"<br/>"+location[i],max_width=100)
                  ).add_to(map_colored)
map_colored